# Importing Packages😁

In [63]:
import numpy as np
import tensorflow as tf
import re
import time
import collections

# Importing the Dataset

#### Dataset Link: https://www.cs.cornell.edu/~cristian/Cornell_Movie-Dialogs_Corpus.html 
##### movie_lines file contains the dialogues of the characters and each dialouge has been given an id
##### movie_conversations file contains a kind of a list of dialogue ids which can make a separate conversation flow

In [64]:
# Importing the dataset
# Reading from the files into a list
lines = open('Data\movie_lines.txt', encoding = 'utf-8', errors = 'ignore').read().split('\n')
conversations = open('Data\movie_conversations.txt', encoding = 'utf-8', errors = 'ignore').read().split('\n')

FileNotFoundError: [Errno 2] No such file or directory: 'Data\\movie_lines.txt'

# Data Preprocessing✌

In [65]:
# Creating a dictionary that maps each line and its id
id2line = {}
for line in lines:
    # Splitting the line to take the necessary elements which are line id and dialogue
    _line = line.split(' +++$+++ ') 
    if len(_line) == 5:
        id2line[_line[0]] = _line[4] # _line[0] specifies the line id and _line[4] specifies the dialogue, thus mapping dialogue to id

##### What we have got so far...

In [66]:
id2line

{'L114493': 'Look at the size of it!',
 'L329193': 'Eric!',
 'L894': 'What?',
 'L511250': 'Excuse me, Miss...  They have a laugh at your expense.',
 'L445613': "C'mon man, didn't I do you right that time I give you the turkey loaf for the ham and lima beans shit.",
 'L345328': "I can't.",
 'L643986': "I'm interested in the Security of My Country, Mr. Brean.",
 'L124957': "That's what he said. Jimmy.",
 'L212325': 'Why are you doing this?',
 'L312023': 'Keep him out of Bedford Falls, anyway.',
 'L292392': '... but it is good.  You know, over to the left, you can ...',
 'L36931': "No. I'm okay.",
 'L339623': 'California.',
 'L130624': "That's worse... Just get out of here. Walk out, leave everything.",
 'L86149': "Carryin' on behind my back. Make me out to look like a fool to all our people. Tell me, what's friendly about that?",
 'L373963': 'Ok.',
 'L134933': "This doesn't even have Burt Reynolds in it.",
 'L491328': "I didn't do it!",
 'L304286': 'Is this "Alice in Wonderland"?',
 'L32

In [67]:
# Creating a list of all of the conversations
conversations_ids = []
for conversation in conversations[:-1]:
    # Splitting the conversations, and formatting them to remove [] and '' and spaces by replacing them with ""
    _conversation = conversation.split(' +++$+++ ')[-1][1:-1].replace("'", "").replace(" ", "")
    conversations_ids.append(_conversation.split(','))

##### We have extracted the line ids of a conversation from the coversations list

In [68]:
conversations_ids

[['L194', 'L195', 'L196', 'L197'],
 ['L198', 'L199'],
 ['L200', 'L201', 'L202', 'L203'],
 ['L204', 'L205', 'L206'],
 ['L207', 'L208'],
 ['L271', 'L272', 'L273', 'L274', 'L275'],
 ['L276', 'L277'],
 ['L280', 'L281'],
 ['L363', 'L364'],
 ['L365', 'L366'],
 ['L367', 'L368'],
 ['L401', 'L402', 'L403'],
 ['L404', 'L405', 'L406', 'L407'],
 ['L575', 'L576'],
 ['L577', 'L578'],
 ['L662', 'L663'],
 ['L693', 'L694', 'L695'],
 ['L696', 'L697', 'L698', 'L699'],
 ['L860', 'L861'],
 ['L862', 'L863', 'L864', 'L865'],
 ['L866', 'L867', 'L868', 'L869'],
 ['L870', 'L871', 'L872'],
 ['L924', 'L925'],
 ['L984', 'L985'],
 ['L1044', 'L1045'],
 ['L49', 'L50', 'L51'],
 ['L571', 'L572', 'L573'],
 ['L579', 'L580'],
 ['L595', 'L596', 'L597'],
 ['L598', 'L599', 'L600'],
 ['L659', 'L660'],
 ['L952', 'L953'],
 ['L394', 'L395'],
 ['L396', 'L397'],
 ['L589', 'L590', 'L591'],
 ['L592', 'L593'],
 ['L756', 'L757', 'L758'],
 ['L759', 'L760'],
 ['L164', 'L165'],
 ['L319', 'L320'],
 ['L441', 'L442', 'L443', 'L444', 'L445']

### Trying to make a question-answer pair using the conversation_ids and id2line lists extracted above🥱

In [69]:
# Making the data into q&a or into two speakers
# One conversation makes len(coversation)-1 Q&A pairs
questions = []
answers = []
for conversation in conversations_ids:
    for i in range(len(conversation)-1):
        questions.append(id2line[conversation[i]])
        answers.append(id2line[conversation[i+1]])

In [70]:
questions

['Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.',
 "Well, I thought we'd start with pronunciation, if that's okay with you.",
 'Not the hacking and gagging and spitting part.  Please.',
 "You're asking me out.  That's so cute. What's your name again?",
 "No, no, it's my fault -- we didn't have a proper introduction ---",
 'Cameron.',
 "The thing is, Cameron -- I'm at the mercy of a particularly hideous breed of loser.  My sister.  I can't date until she does.",
 'Why?',
 'Unsolved mystery.  She used to be really popular when she started high school, then it was just like she got sick of it or something.',
 'Gosh, if only we could find Kat a boyfriend...',
 "C'esc ma tete. This is my head",
 "Right.  See?  You're ready for the quiz.",
 "I don't want to know how to say that though.  I want to know useful things. Like where the good stores are.  How much does champagne cost?  Stuff like Chat.  I have n

In [71]:
answers

["Well, I thought we'd start with pronunciation, if that's okay with you.",
 'Not the hacking and gagging and spitting part.  Please.',
 "Okay... then how 'bout we try out some French cuisine.  Saturday?  Night?",
 'Forget it.',
 'Cameron.',
 "The thing is, Cameron -- I'm at the mercy of a particularly hideous breed of loser.  My sister.  I can't date until she does.",
 'Seems like she could get a date easy enough...',
 'Unsolved mystery.  She used to be really popular when she started high school, then it was just like she got sick of it or something.',
 "That's a shame.",
 'Let me see what I can do.',
 "Right.  See?  You're ready for the quiz.",
 "I don't want to know how to say that though.  I want to know useful things. Like where the good stores are.  How much does champagne cost?  Stuff like Chat.  I have never in my life had to point out my head to someone.",
 "That's because it's such a nice one.",
 'Forget French.',
 "Well, there's someone I think might be --",
 'Where?',
 "I 

#### We define a function clean_text which changes the data to lower case to avoid dealing with case sensitive issues. 
#### Once that is done we convert all the words concatenated via an apostrophe into their respective words. 
#### We also replace special characters and brackets with ""

In [72]:
def clean_text(text):
    text = text.lower()
    text = re.sub(r"i'm", "i am", text)
    text = re.sub(r"he's", "he is", text)
    text = re.sub(r"she's", "she is", text)
    text = re.sub(r"don't", "do not", text)
    text = re.sub(r"can't", "can not", text)
    text = re.sub(r"didn't", "did not", text)
    text = re.sub(r"that's", "that is", text)
    text = re.sub(r"what's", "what is", text)
    text = re.sub(r"we'd", "we would", text)
    text = re.sub(r"where's", "where is", text)
    text = re.sub(r"\'ll", " will", text)
    text = re.sub(r"\'ve", " have", text)
    text = re.sub(r"\'re", " are", text)
    text = re.sub(r"\'d", " would", text)
    text = re.sub(r"[-()\"#/@;:<>+-=~|.,?]", "", text)
    return text

In [73]:
# Cleaning Questions
questions_new = []
for q in questions:
    questions_new.append(clean_text(q))

In [74]:
# Cleaning Answers
answers_new = []
for a in answers:
    answers_new.append(clean_text(a))

### We now find the number of occurences of a word in both the questions and the answers. The idea being the least frequent words can be filtered out later.

In [75]:
# Implemented using dictionary
word2count = {}
for question in questions_new:
    for word in question.split():
        if word not in word2count:
            word2count[word] = 1
        else:
            word2count[word] += 1
for answer in answers_new:
    for word in answer.split():
        if word not in word2count:
            word2count[word] = 1
        else:
            word2count[word] += 1

In [76]:
word2count

{'mercea': 4,
 'minoxidil': 1,
 'grooming': 8,
 'widescreen': 2,
 'fence!': 2,
 'david': 448,
 "heartbeatit's": 2,
 'timethe': 2,
 "'amazombies'": 1,
 'eeeww': 2,
 'schemer': 3,
 'potheads': 1,
 'hourly': 3,
 'sirbut': 4,
 'haguelost': 1,
 'rotor': 2,
 'sausalito': 5,
 'kirkland': 4,
 'martyr': 12,
 'sro': 2,
 'corey': 17,
 'timeshell': 2,
 'tells': 300,
 'alcohol': 47,
 'medkit': 3,
 'mondays': 5,
 "pipin'": 2,
 'touchdown': 11,
 'observes': 1,
 "cousin's": 4,
 'riggins': 1,
 'eppsepps!': 2,
 'subconscious': 22,
 'claudette': 6,
 'beef': 80,
 'saysyou': 2,
 'bakersfield': 4,
 'electrify': 1,
 'teardrops': 4,
 "knowlet's": 2,
 "a'that": 1,
 'roaring': 8,
 'sweaters!': 1,
 'woodson': 1,
 'youhow': 2,
 'parent': 31,
 'ballard': 9,
 '[to': 1,
 'shmoe!': 1,
 'somehowdo': 1,
 'dipper': 7,
 'sexpot': 2,
 'worker!!!': 1,
 'scary!': 2,
 'inserted': 9,
 'nile': 1,
 'recanted': 2,
 'richwhiteman': 2,
 'bootlicking': 1,
 'halffive': 1,
 'viva': 2,
 'captains': 11,
 'senateuhwhat': 2,
 'fourfooted

#### Finding the most frequent count for a word

In [77]:
Keymax = max(word2count, key=word2count.get) 
print(Keymax) 
all_values = word2count.values()
max_value = max(all_values)
print(max_value)

you
212945


In [78]:
Keymax = min(word2count, key=word2count.get) 
print(Keymax) 
all_values = word2count.values()
max_value = min(all_values)
print(max_value)

minoxidil
1


In [79]:
len(word2count)

75116

## Remove the less frequent words and map all words to a unique integer🚓
#### We can't use the dataset directly. We need to split the sentences into words and convert it into One-Hot Vector. Then create a dictionary by indexing every unknown word for Sequence to sequence models.

In [80]:
# Creating two dictionaries that map the questions words and the answers words to a unique integer
# The process does the removal of less frequent words
# https://www.guru99.com/seq2seq-model.html
threshold = 15
questionswords2int = {}
word_number = 0
for word, count in word2count.items():
    if count > threshold:
        questionswords2int[word]= word_number
        word_number += 1
answerswords2int = {}
word_number = 0
for word, count in word2count.items():
    if count > threshold:
        answerswords2int[word]= word_number
        word_number += 1

In [81]:
# Adding the last tokens to these two dictionaries
# https://towardsdatascience.com/sequence-to-sequence-model-introduction-and-concepts-44d9b41cd42d
tokens = ['<PAD>', '<EOS>', '<OUT>', '<SOS>']
for token in tokens:
    questionswords2int[token] = len(questionswords2int) + 1
for token in tokens:
    answerswords2int[token] = len(answerswords2int) + 1

In [82]:
questionswords2int

{'cooling': 6471,
 'fork': 5107,
 'private': 8653,
 'affect': 9053,
 'bottles': 6901,
 'paintings': 9055,
 'david': 0,
 'pretend': 7769,
 'rules!': 9884,
 'peaceful': 7770,
 "stayin'": 8641,
 'glasses': 1361,
 'compliments': 10081,
 'enquirer': 4756,
 'affairs': 7771,
 'capital': 5587,
 'docks': 7113,
 'clemenza': 7772,
 'sinking': 2628,
 'seduce': 2629,
 'youand': 1362,
 'pissed': 1970,
 'socks': 6472,
 'corey': 1,
 'cloak': 5115,
 'im': 1364,
 'tells': 2,
 'alcohol': 3,
 'shoulder': 6474,
 'lucy': 2650,
 'hull': 3904,
 'getaway': 1365,
 'subconscious': 4,
 'herbert': 7773,
 "aren't": 5108,
 'witnesses': 1366,
 'simpler': 9856,
 'ancestors': 6477,
 "ain't": 5109,
 'worst': 8654,
 'wrong': 1367,
 'trigger': 5110,
 'utter': 2630,
 'search': 5111,
 'cadet': 1368,
 'chang': 6478,
 "o'brien": 2631,
 'parent': 6,
 'stamps': 7775,
 'pal': 5870,
 'stepping': 7776,
 'found': 1360,
 'presented': 6544,
 'breeding': 2632,
 'windows': 5112,
 'promotion': 1369,
 'tell': 2526,
 'nightmares': 9056,
 

In [83]:
questionswords2int['<PAD>']

10305

### Since, we should be able to find the index of a word or find a word from its index.
### Hence we will create an inverse dictionary for answerswords2int and questionswords2int

In [84]:
answersint2word = {w_i: w for w, w_i in answerswords2int.items()}
questionsint2word = {w_i: w for w, w_i in questionswords2int.items()}
# Adding the End Of String token to the end of every cleaned answer created previously
for i in range(len(answers_new)):
    answers_new[i] += ' <EOS>'

### Now after mapping each word to a unique integer, we should be able to convert our Q&A's into a sequence of integers; just how our model would like it to be 
#### PS: Model can understand only numbers and not text😅


In [85]:
questions_into_int = []
for question in questions_new:
    ints = []
    for word in question.split():
        if word not in questionswords2int:
            ints.append(questionswords2int['<OUT>']) #replacing less frequent words with a token
        else:
            ints.append(questionswords2int[word])
    questions_into_int.append(ints)
answers_into_int = []
for answer in answers_new:
    ints = []
    for word in answer.split():
        if word not in answerswords2int:
            ints.append(answerswords2int['<OUT>'])
        else:
            ints.append(answerswords2int[word])
    answers_into_int.append(ints)

In [86]:
questions_into_int

[[5559,
  9298,
  1589,
  6680,
  7619,
  10307,
  10307,
  9040,
  5924,
  817,
  1578,
  7326,
  99,
  5370,
  10307,
  10168,
  8055,
  1666,
  3116,
  1265,
  10307,
  842],
 [3487,
  5434,
  2931,
  9298,
  2356,
  5796,
  2444,
  10307,
  3683,
  8068,
  4094,
  1104,
  2444,
  7336],
 [9288, 1265, 9338, 9040, 10307, 9040, 750, 849, 9493],
 [7336,
  1578,
  562,
  1870,
  5867,
  8068,
  4094,
  7438,
  1119,
  5144,
  4094,
  5447,
  7696,
  842],
 [240, 240, 5176, 10041, 3393, 9298, 6485, 9288, 3307, 6907, 1577, 136],
 [2427],
 [1265,
  5168,
  4094,
  2427,
  5434,
  5660,
  7303,
  1265,
  2056,
  6200,
  6907,
  1956,
  6895,
  5615,
  6200,
  3442,
  10041,
  2442,
  5434,
  5559,
  9288,
  9286,
  1902,
  2911,
  4559],
 [746],
 [4070,
  3677,
  2911,
  3176,
  7754,
  8543,
  9604,
  9017,
  4342,
  2911,
  566,
  1448,
  4489,
  9245,
  3148,
  2684,
  8067,
  8946,
  2911,
  5453,
  3846,
  6200,
  3148,
  2784,
  7308],
 [3361, 3683, 8020, 9298, 5135, 5237, 7372, 6907,

In [87]:
## For Understanding the next step
for i in enumerate(questions_into_int):
    print (i)

(0, [5559, 9298, 1589, 6680, 7619, 10307, 10307, 9040, 5924, 817, 1578, 7326, 99, 5370, 10307, 10168, 8055, 1666, 3116, 1265, 10307, 842])
(1, [3487, 5434, 2931, 9298, 2356, 5796, 2444, 10307, 3683, 8068, 4094, 1104, 2444, 7336])
(2, [9288, 1265, 9338, 9040, 10307, 9040, 750, 849, 9493])
(3, [7336, 1578, 562, 1870, 5867, 8068, 4094, 7438, 1119, 5144, 4094, 5447, 7696, 842])
(4, [240, 240, 5176, 10041, 3393, 9298, 6485, 9288, 3307, 6907, 1577, 136])
(5, [2427])
(6, [1265, 5168, 4094, 2427, 5434, 5660, 7303, 1265, 2056, 6200, 6907, 1956, 6895, 5615, 6200, 3442, 10041, 2442, 5434, 5559, 9288, 9286, 1902, 2911, 4559])
(7, [746])
(8, [4070, 3677, 2911, 3176, 7754, 8543, 9604, 9017, 4342, 2911, 566, 1448, 4489, 9245, 3148, 2684, 8067, 8946, 2911, 5453, 3846, 6200, 3148, 2784, 7308])
(9, [3361, 3683, 8020, 9298, 5135, 5237, 7372, 6907, 1992])
(10, [10307, 44, 10307, 6680, 4094, 10041, 745])
(11, [4715, 4013, 7336, 1578, 677, 7432, 1265, 10307])
(12, [5434, 6088, 9288, 9258, 7754, 6195, 2861, 

(2734, [5434, 4026, 1745, 10307, 10008, 2566, 5347, 7336, 10307, 7303, 1265, 5513, 6485, 9288, 3533])
(2735, [5434, 4026])
(2736, [6286, 6200, 1265, 6404, 547, 9040, 3458, 8949, 6907, 2942, 758, 1802, 1265, 8576, 5259, 6200, 1265, 6119, 1802, 7288, 7947, 7679, 3533, 2138, 2295, 4067, 9040, 7245, 290, 8946, 6907, 7062, 7754, 6121, 1815, 3332])
(2737, [7438])
(2738, [7438, 7782, 6200, 6907, 2370, 3688, 8020, 4677, 4895, 5867, 6200, 4489, 8543, 10307, 1291, 4867, 8946, 6907, 10307, 6907, 2942, 10307, 10307, 9040, 10307, 10307, 1265, 1815, 10307, 7656, 1265, 3953, 10307, 9299, 1265, 10307, 10307, 10307, 10307])
(2739, [570, 10307, 3043, 9288, 1745, 10307, 7346, 3148, 7026, 3688, 2728, 9245, 4342, 4915, 6532, 3115, 9158, 9441, 7112, 8916, 4677, 6200, 6907, 10307, 10307, 5215, 10307, 594, 8644, 1265, 5753, 7732, 3533, 2594, 1454, 3688, 7664, 1802, 1442, 3189, 2444, 94, 8946, 1265, 10307, 570, 3148, 7026, 4434, 7782, 1265, 6844])
(2740, [3307, 7336, 8836, 7662, 7754, 9158, 3213, 7754, 4013, 3

(5234, [3148, 5574, 6907, 7976])
(5235, [5434, 40, 5447, 7605])
(5236, [3148, 2684, 6907, 9816])
(5237, [5144])
(5238, [634, 10307])
(5239, [7931])
(5240, [7336, 7109, 2993, 5447, 9580])
(5241, [5434, 5660, 9288, 741, 1459, 7594, 7336])
(5242, [5434, 5660, 8803, 7336, 3307, 7754, 8217, 7308])
(5243, [9493, 9604, 5434, 5660, 9288, 1459])
(5244, [7336, 6494, 1870, 1802, 99, 1200, 3634, 634, 10307])
(5245, [2861, 4094, 8068])
(5246, [3487, 7336, 1578, 7754, 8642, 2096, 9831, 7336, 3307, 2993, 2797, 5144, 7951, 6200, 9860, 2356, 5434, 8543, 3683, 5434, 8240, 1802, 7438, 80, 6907, 9995, 4879, 1471, 5867, 4915, 7339])
(5247, [3528, 1265, 7339, 5434, 4516, 8642, 9326, 7719])
(5248, [5616, 4803, 3116, 7977, 10307])
(5249, [9514, 1870, 9812])
(5250, [5616, 4803, 3116, 10307])
(5251, [9514, 1870, 0])
(5252, [267, 5434, 8543, 8177, 7754, 5127, 7336, 0])
(5253, [6680, 4094, 5958, 5434, 5660, 9288, 1459, 5434, 6088, 9288, 9258, 2378, 3987])
(5254, [1889, 2848, 6907, 3830, 5863, 267, 9298])
(5255, [

(8133, [318, 5453, 99, 2258, 352, 7754, 1589])
(8134, [5144])
(8135, [5301, 4154, 1889, 3007, 6907, 2345, 2581, 2444, 6884, 5594, 9040, 2992])
(8136, [4920, 4094, 1265, 6726, 4154, 9298, 9317, 3307, 6726])
(8137, [10307, 6286, 5168, 7303, 6907, 4336])
(8138, [5434, 6088, 9288, 4931, 3148, 570, 7303, 6401, 10307, 5453, 1265, 2942, 8325, 4139, 1666, 8686, 1802, 6907, 5729, 8147])
(8139, [5985, 7336, 7568, 5144, 4094, 587, 3116])
(8140, [9298, 1578, 587, 7432, 6907, 3830, 3962, 10307])
(8141, [5434, 3307, 8692, 9288, 7754, 4041, 7432, 4546])
(8142, [4154, 7336, 1578, 1386, 5447, 453])
(8143, [7931, 7510, 9977, 9831, 5241, 5434, 5758, 10041, 1581, 3891, 9040, 5830, 3561])
(8144, [7336, 6641, 10307, 5453, 6680, 6212, 2581, 6236, 5638])
(8145, [5301, 4154, 3533, 4094, 5453, 2295, 6907, 2236, 4453, 7303, 1265, 3655, 9040, 767, 6200, 727])
(8146, [5434, 9413, 7438, 8200, 6662, 380, 4094, 6907, 5878, 6200, 10307])
(8147, [7782, 3539])
(8148, [10307, 2986, 2236, 10307, 337])
(8149, [9040])
(8150

(10733, [10190])
(10734, [7336, 6485, 9288, 3342, 1870, 4183, 10307])
(10735, [1593])
(10736, [5434, 5660, 4106])
(10737, [5176, 9288, 7551])
(10738, [5176, 9288, 7551, 9479])
(10739, [746])
(10740, [5434, 5660, 9288, 562, 7336, 7754, 3972, 1870])
(10741, [240, 5144, 240, 5434, 6195])
(10742, [5176, 9834, 8946, 6907, 9286])
(10743, [5176, 6907, 6317, 3779, 7754, 8633, 7432, 6907, 9286])
(10744, [5144, 4559, 3148, 9363])
(10745, [1140, 5434, 4516, 4998, 7432, 7336, 8686])
(10746, [10041, 7153, 2298])
(10747, [4094, 1265, 8896, 3656])
(10748, [5434, 5660, 4106, 8041, 5434, 6221, 1265, 8896, 4094, 4626])
(10749, [7336, 3307, 7320, 4119])
(10750, [2073])
(10751, [2861, 6088, 7336, 9258, 7754, 7186])
(10752, [5144, 1578, 7336, 8389])
(10753, [8067, 3396, 7754, 4013])
(10754, [7336, 6195, 1265, 7907, 7336, 6088, 6195, 1265, 7907, 6088, 9288, 7336])
(10755, [5301, 5434, 6195])
(10756, [9245, 5796, 7581, 9326, 870])
(10757, [10307])
(10758, [8696, 7001, 1870, 6907, 5796])
(10759, [5434, 5660, 

...

(75222, [7732, 5434, 5660, 4106, 2861, 2356, 5447, 10181, 8642, 3148])
(75223, [5434, 7109, 5226, 99, 9896, 240, 8235])
(75224, [7336, 7109, 3613, 9245, 3443])
(75225, [240])
(75226, [5434, 5660, 982, 7581, 6907, 6891, 4879, 6907, 2682])
(75227, [5434, 5226, 3148, 3409, 9772, 4786, 7754, 4268, 7432, 8068, 3901])
(75228, [5434, 6195, 5144, 7336, 1578, 8451, 4154, 5434, 6088, 9288, 6195, 5144, 7754, 2526, 7336])
(75229, [6858, 558, 9298, 1659, 7001, 1666, 3116, 7336])
(75230, [7732, 1578, 9298, 4614, 963, 1578, 240, 10307, 1802, 6680, 7143])
(75231, [240, 240, 1265, 8654, 2684, 4342, 5434, 7257, 1802, 7432, 6680, 10307, 5798, 9040, 5434, 5660, 7203, 1802, 1265, 4616, 4453, 2444, 7782, 2096, 3830, 5343, 5434, 4013, 124, 1578, 7782, 2852, 1802, 7432, 1265, 6844, 4861, 4879, 1870])
(75232, [124, 5841, 10307, 7432, 1265, 6844, 4861, 4879, 7336])
(75233, [5176, 8946, 7336, 7677, 7303, 10041, 6374, 7336, 9432, 10041, 3870, 746, 6485, 7336, 9514, 1870, 1802, 7336, 2663, 5434, 2684, 2670])
(7523

(78222, [2861])
(78223, [2861, 6088, 7336, 5847, 7754, 6088, 8068])
(78224, [2861, 5559, 9298, 8633, 3116, 5021, 8686, 3683, 9298, 8682, 1265, 7143, 2444, 8263])
(78225, [5922, 4268, 3116, 1265, 5014])
(78226, [8287])
(78227, [5301, 8287, 7782, 124, 6088, 4094, 1589, 6907, 1643, 6200, 4700, 3802, 4946, 9326])
(78228, [9298, 2152, 9326])
(78229, [9288, 3683, 124, 1578, 2542, 6907, 7947])
(78230, [9245, 4688, 4130, 4931, 362, 420, 9040, 8484, 9326, 1144, 1265, 37, 6200, 1265, 1241])
(78231, [2156, 9326, 7782, 4931, 7817, 6200, 9326, 7295, 5903])
(78232, [8068, 4094, 4715, 8041, 5434, 5310, 3148, 6907, 8098, 10307, 6200, 10307, 5453, 2825, 1802, 6907, 3272, 9040, 6967, 1802, 7432, 1265, 7143, 4920, 7782, 1265, 2107, 5841])
(78233, [124, 3838, 4915, 1643, 499, 1110, 4791, 2999, 9040, 4700, 124, 8702, 1589, 6907, 1643, 9298, 1578, 6407, 1144, 2369, 9326])
(78234, [2861, 6232, 10307, 6485, 7336, 2472, 5253, 3011])
(78235, [5057, 10307, 634, 10307, 963, 1578, 143, 10307])
(78236, [1265, 1627,

(81221, [3487, 5301, 5434, 6485, 9288, 6195, 924, 47, 4434, 5434, 8067, 2931])
(81222, [595, 5434, 9250, 5434, 5574, 1670, 7754, 1211, 7336])
(81223, [9245, 5144, 1265, 2945, 6485, 7336, 6088, 3148, 7432])
(81224, [9493, 3528])
(81225, [595, 4803, 3116])
(81226, [10134])
(81227, [10307, 9040, 5434, 7257, 5867, 7432, 2398, 1802, 1448, 4489])
(81228, [5144, 5144, 1578, 7336, 8389, 8686])
(81229, [10011])
(81230, [5434, 5434, 8067, 9258, 7336, 7754, 8543, 7757, 595])
(81231, [570, 570, 5144, 47, 10201])
(81232, [4931, 5100, 8686])
(81233, [9604])
(81234, [5301, 5144, 6088, 7336, 9258])
(81235, [3492, 6858, 5434, 5660, 10011, 10307, 5434, 5660, 8686, 7754, 8642, 595, 7754, 1265, 7123])
(81236, [2755, 4443, 2484, 5144, 1265, 1637, 5841, 7336, 6757])
(81237, [5144, 7030, 7754, 8543, 1265, 5046, 8686, 7336, 7996, 7897, 2784, 7308])
(81238, [5434, 8185, 5434, 5453, 3148, 4751])
(81239, [7336, 5453, 5144, 4751])
(81240, [3148])
(81241, [7732, 7432, 1265, 5531, 6200, 4967])
(81242, [10307])
(812

(84721, [5144])
(84722, [5144, 4094, 3148, 587, 7754, 8543])
(84723, [5434, 5660, 4106])
(84724, [5144, 1578, 7336, 10307, 47])
(84725, [6088, 9288, 6138, 5200, 6138, 1802, 10041, 3106, 10307, 9298, 4516, 6088, 3148, 5638])
(84726, [5434, 5559, 9288])
(84727, [7336, 4866, 3438, 3148, 2784, 7438, 1281, 1870, 5434, 4516, 9925, 7336, 7754, 1265, 10307, 4976, 5447, 10307, 9040, 3528, 7336, 7522])
(84728, [1578, 7336, 1909, 7298, 1578, 561])
(84729, [5434, 9448, 7336, 7336, 4677, 6200, 6907, 10307])
(84730, [4094, 3148, 2085, 8068, 7336, 8177, 5353, 6114, 7754, 4866, 1265, 5920, 4342, 3148, 2684, 10000, 8068, 3533, 2684, 10307])
(84731, [3533, 7695, 4342, 3533, 2684, 677])
(84732, [8041, 5841, 7336, 8234, 7303, 2378, 4336, 6200, 1265, 9697, 6200, 3, 3177, 1265, 1128])
(84733, [240])
(84734, [5144, 2986, 7336, 7438, 6641, 3148, 2684, 6286])
(84735, [5434, 5559, 9288, 8543, 6641])
(84736, [7336, 9604, 9197, 8068, 5447, 1128, 5841, 1666, 7432, 1265, 783])
(84737, [9298, 2356, 4803, 6199, 6585,

KeyboardInterrupt: 

## Two operations are being performed in the following cell:
#### 1) We are limiting the length of questions and answers to filter out the questions and answers that are too long
#### 2) We are sorting the questions and answers by their length

In [88]:
sorted_clean_questions = []
sorted_clean_answers = []
for length in range(1, 25 + 1):
    for i in enumerate(questions_into_int):
        if len(i[1]) == length:
            sorted_clean_questions.append(questions_into_int[i[0]])
            sorted_clean_answers.append(answers_into_int[i[0]])

In [89]:
(sorted_clean_questions)

[[2427],
 [746],
 [963],
 [6858],
 [570],
 [240],
 [1999],
 [240],
 [3802],
 [2236],
 [2161],
 [5144],
 [746],
 [570],
 [746],
 [2410],
 [2996],
 [6641],
 [9813],
 [5301],
 [5144],
 [5985],
 [3802],
 [1104],
 [746],
 [3802],
 [10307],
 [5964],
 [4762],
 [3802],
 [5818],
 [10307],
 [10307],
 [7931],
 [2861],
 [10307],
 [10307],
 [5144],
 [240],
 [5144],
 [10307],
 [6858],
 [4715],
 [5144],
 [8774],
 [10307],
 [4834],
 [240],
 [240],
 [5537],
 [10307],
 [66],
 [240],
 [7732],
 [4342],
 [5301],
 [240],
 [2225],
 [3600],
 [5301],
 [622],
 [622],
 [622],
 [622],
 [5301],
 [6302],
 [348],
 [1104],
 [677],
 [7931],
 [5144],
 [7800],
 [630],
 [10307],
 [10307],
 [844],
 [5301],
 [3020],
 [5144],
 [5144],
 [5301],
 [8030],
 [8030],
 [8030],
 [8030],
 [8030],
 [8030],
 [1104],
 [7931],
 [9604],
 [7931],
 [7732],
 [2861],
 [9568],
 [8030],
 [8030],
 [8030],
 [10307],
 [8030],
 [8030],
 [9604],
 [8453],
 [2085],
 [7718],
 [5301],
 [7696],
 [5301],
 [5003],
 [5301],
 [1336],
 [5301],
 [3487],
 [963

# Preprocessing Completed😴

# Starting To Build a model 

In [90]:
# Creating Placeholders for inputs and targets
# Tensors need to be held in placeholders to be used in Tensorflow

def model_inputs():
    inputs = tf.placeholder(tf.int32, [None, None], name = 'input')
    targets = tf.placeholder(tf.int32, [None, None], name = 'target')
    lr = tf.placeholder(tf.float32, name='learning_rate')
    keep_prob = tf.placeholder(tf.float32, name='keep_prob')
    return inputs, targets, lr, keep_prob


In [91]:
# Pre-process Target

def preprocess_targets(targets, word2int, batch_size):
    left_side = tf.fill([batch_size, 1], word2int['<SOS>'] )
    right_side = tf.strided_slice(targets, [0,0], [batch_size, -1], [1,1])
    preprocessed_targets = tf.concat([left_side, right_side],1)
    return preprocessed_targets


In [92]:
# Encoder RNN - Stacked LSTM with Dropout
def encoder_rnn_layer(rnn_inputs, rnn_size, num_layers, keep_prob, sequence_length):
    lstm = tf.contrib.rnn.BasicLSTMCell(rnn_size)
    lstm_dropout = tf.contrib.rnn.DropoutWrapper(lstm, input_keep_prob= keep_prob)
    encoder_cell = tf.contrib.rnn.MultiRNNCell([lstm_dropout]*num_layers)
    _, encoder_state = tf.nn.bidirectional_dynamic_rnn(cell_fw = encoder_cell, 
                                                       cell_bw= encoder_cell,
                                                       sequence_length = sequence_length,
                                                       inputs = rnn_inputs,
                                                       dtype = tf.float32)
    return encoder_state

In [93]:
def decode_training_set(encoder_state, decoder_cell, decoder_embedded_input, 
                        sequence_length, decoding_scope, output_function, 
                        keep_prob, batch_size):
    attention_states = tf.zeros([batch_size, 1, decoder_cell.output_size])
    attention_keys, attention_values, attention_score_function, attention_construct_function = tf.contrib.seq2seq.prepare_attention(attention_states, 
                                                                        attention_option = 'bahdanau', 
                                                                        num_units = decoder_cell.output_size)
    training_decoder_function = tf.contrib.seq2seq.attention_decoder_fn_train(encoder_state[0],
                                                                              attention_keys,
                                                                              attention_values,
                                                                              attention_score_function,
                                                                              attention_construct_function,
                                                                              name = 'attn_dec_train')
    decoder_output, decoder_final_state, decoder_final_context_state = tf.contrib.seq2seq.dynamic_rnn_decoder(decoder_cell, 
                                                                                                              training_decoder_function,
                                                                                                              decoder_embedded_input,
                                                                                                              sequence_length,
                                                                                                              scope = decoding_scope)
    decoder_output_drop= tf.nn.dropout(decoder_output, keep_prob)
    return output_function(decoder_output_drop)


In [94]:
# Decoding Test/Validation Set
def decode_test_set(encoder_state, decoder_cell, decoder_embedded_matrix, 
                    sos_id, eos_id, maximum_length, num_words,
                    decoding_scope, output_function, keep_prob, batch_size):
    attention_states = tf.zeros([batch_size, 1, decoder_cell.output_size])
    attention_keys, attention_values, attention_score_function, attention_construct_function = tf.contrib.seq2seq.prepare_attention(attention_states, 
                                                                        attention_option = 'bahdanau', 
                                                                        num_units = decoder_cell.output_size)
    test_decoder_function = tf.contrib.seq2seq.attention_decoder_fn_inference(output_function,
                                                                              encoder_state[0],
                                                                              attention_keys,
                                                                              attention_values,
                                                                              attention_score_function,
                                                                              attention_construct_function,
                                                                              decoder_embedded_matrix, sos_id, 
                                                                              eos_id, 
                                                                              maximum_length, 
                                                                              num_words,
                                                                              name = 'attn_dec_inf')
    test_prediction, decoder_final_state, decoder_final_context_state = tf.contrib.seq2seq.dynamic_rnn_decoder(decoder_cell, 
                                                                                                              test_decoder_function,
                                                                                                              scope = decoding_scope)
    return test_prediction

In [95]:
# Decoder RNN
def decoder_rnn(decoder_embedded_input, decoder_embedded_matrix, encoder_state, num_words, 
                sequence_length, rnn_size, num_layers, word2int, keep_prob, batch_size ):
    with tf.variable_scope('decoding') as decoding_scope:
        lstm = tf.contrib.rnn.BasicLSTMCell(rnn_size)
        lstm_dropout = tf.contrib.rnn.DropoutWrapper(lstm, input_keep_prob= keep_prob)
        decoder_cell = tf.contrib.rnn.MultiRNNCell([lstm_dropout]*num_layers)
        weights = tf.truncated_normal_initializer(stddev=0.1)
        biases = tf.zeros_initializer()
        output_function = lambda x: tf.contrib.layers.fully_connected(x,
                                                                      num_words,
                                                                      None,
                                                                      scope=decoding_scope,
                                                                      weights_initializer=weights,
                                                                      biases_initializer=biases)
        training_predictions = decode_training_set(encoder_state,
                                                   decoder_cell,
                                                   decoder_embedded_input,
                                                   sequence_length,
                                                   decoding_scope,
                                                   output_function,
                                                   keep_prob,
                                                   batch_size)
        decoding_scope.reuse_variables()
        test_predictions = decode_test_set(encoder_state,
                                           decoder_cell,
                                           decoder_embedded_matrix,
                                           word2int['<SOS>'],
                                           word2int['<EOS>'],
                                           sequence_length - 1,
                                           num_words,
                                           decoding_scope,
                                           output_function,
                                           keep_prob,
                                           batch_size)
        return training_predictions, test_predictions


In [96]:
# Building Seq2Seq
    
def seq2seq_model(inputs,targets, keep_prob, batch_size, sequence_length, answers_num_words, questions_num_words,
                  encoder_embedding_size, decoder_embedding_size, rnn_size, num_layers, questionswords2int):
    encoder_embedded_input = tf.contrib.layers.embed_sequence(inputs,
                                                              answers_num_words+1,
                                                              encoder_embedding_size,
                                                              initializer = tf.random_uniform_initializer(0,1))
    encoder_state = encoder_rnn_layer(encoder_embedded_input, rnn_size, num_layers, keep_prob, sequence_length)
    preprocessed_targets = preprocess_targets(targets, questionswords2int, batch_size)
    decoder_embedded_matrix = tf.Variable(tf.random_uniform([questions_num_words+1, decoder_embedding_size], 0, 1))
    decoder_embedded_input = tf.nn.embedding_lookup(decoder_embedded_matrix, preprocessed_targets)
    training_predictions, test_predictions = decoder_rnn(decoder_embedded_input, decoder_embedded_matrix,
                                                         encoder_state,
                                                         questions_num_words,
                                                         sequence_length,
                                                         rnn_size,
                                                         num_layers,
                                                         questionswords2int,
                                                         keep_prob,
                                                         batch_size)
    return training_predictions, test_predictions

In [97]:
# Hyperparameter Settings
    
epochs =  100
batch_size = 32
rnn_size = 1024
num_layers = 3
encoding_embedding_size = 1024
decoding_embedding_size = 1024
learning_rate = 0.001
learning_rate_decay = 0.9
min_learning_rate = 0.0001
keep_probability = 0.5

In [98]:
# Defining a tf session
tf.reset_default_graph()
session= tf.InteractiveSession()

In [99]:
# Load model inputs

inputs, targets, lr, keep_prob = model_inputs()

In [100]:
#Setting Sequence Length

sequence_length = tf.placeholder_with_default(25, None, name = 'sequence_length') 
# We set this in the data preprocessing as 25

In [101]:
# Getting shape of input tensor

input_shape = tf.shape(inputs)

In [102]:
training_predictions, test_predictions = seq2seq_model(tf.reverse(inputs,[-1]), 
                                                                  targets,
                                                                  keep_prob,
                                                                  batch_size,
                                                                  sequence_length,
                                                                  len(answerswords2int),
                                                                  len(questionswords2int),
                                                                  encoding_embedding_size,
                                                                  decoding_embedding_size,
                                                                  rnn_size,
                                                                  num_layers,
                                                                  questionswords2int)

In [103]:
# Setting up the Loss Error, the Optimizer and Gradient Clipping
with tf.name_scope("optimization"):
    loss_error = tf.contrib.seq2seq.sequence_loss(training_predictions,
                                                  targets,
                                                  tf.ones([input_shape[0], sequence_length]))
    optimizer = tf.train.AdamOptimizer(learning_rate)
    gradients = optimizer.compute_gradients(loss_error)
    clipped_gradients = [(tf.clip_by_value(grad_tensor, -5., 5.), grad_variable) for grad_tensor, grad_variable in gradients if grad_tensor is not None]
    optimizer_gradient_clipping = optimizer.apply_gradients(clipped_gradients)
 

In [104]:
# Padding the sequences with the <PAD> token
def apply_padding(batch_of_sequences, word2int):
    max_sequence_length = max([len(sequence) for sequence in batch_of_sequences])
    return [sequence + [word2int['<PAD>']] * (max_sequence_length - len(sequence)) for sequence in batch_of_sequences]

In [105]:
# Splitting the data into batches of questions and answers
def split_into_batches(questions, answers, batch_size):
    for batch_index in range(0, len(questions) // batch_size):
        start_index = batch_index * batch_size
        questions_in_batch = questions[start_index : start_index + batch_size]
        answers_in_batch = answers[start_index : start_index + batch_size]
        padded_questions_in_batch = np.array(apply_padding(questions_in_batch, questionswords2int))
        padded_answers_in_batch = np.array(apply_padding(answers_in_batch, answerswords2int))
        yield padded_questions_in_batch, padded_answers_in_batch
 

In [106]:
# Splitting the questions and answers into training and validation sets
training_validation_split = int(len(sorted_clean_questions) * 0.15)
training_questions = sorted_clean_questions[training_validation_split:]
training_answers = sorted_clean_answers[training_validation_split:]
validation_questions = sorted_clean_questions[:training_validation_split]
validation_answers = sorted_clean_answers[:training_validation_split]
 
# Training
batch_index_check_training_loss = 100
batch_index_check_validation_loss = ((len(training_questions)) // batch_size // 2) - 1
total_training_loss_error = 0
list_validation_loss_error = []
early_stopping_check = 0
early_stopping_stop = 100
checkpoint = "Data/chatbot_weights.ckpt"
session.run(tf.global_variables_initializer())

In [ ]:

for epoch in range(1, 2):
    for batch_index, (padded_questions_in_batch, padded_answers_in_batch) in enumerate(split_into_batches(training_questions, training_answers, batch_size)):
        starting_time = time.time()
        _, batch_training_loss_error = session.run([optimizer_gradient_clipping, loss_error], {inputs: padded_questions_in_batch,
                                                                                               targets: padded_answers_in_batch,
                                                                                               lr: learning_rate,
                                                                                               sequence_length: padded_answers_in_batch.shape[1],
                                                                                               keep_prob: keep_probability})
        total_training_loss_error += batch_training_loss_error
        ending_time = time.time()
        batch_time = ending_time - starting_time
        if batch_index % batch_index_check_training_loss == 0:
            print('Epoch: {:>3}/{}, Batch: {:>4}/{}, Training Loss Error: {:>6.3f}, Training Time on 100 Batches: {:d} seconds'.format(epoch,
                                                                                                                                       epochs,
                                                                                                                                       batch_index,
                                                                                                                                       len(training_questions) // batch_size,
                                                                                                                                       total_training_loss_error / batch_index_check_training_loss,
                                                                                                                                       int(batch_time * batch_index_check_training_loss)))
            total_training_loss_error = 0
        if batch_index % batch_index_check_validation_loss == 0 and batch_index > 0:
            total_validation_loss_error = 0
            starting_time = time.time()
            for batch_index_validation, (padded_questions_in_batch, padded_answers_in_batch) in enumerate(split_into_batches(validation_questions, validation_answers, batch_size)):
                batch_validation_loss_error = session.run(loss_error, {inputs: padded_questions_in_batch,
                                                                       targets: padded_answers_in_batch,
                                                                       lr: learning_rate,
                                                                       sequence_length: padded_answers_in_batch.shape[1],
                                                                       keep_prob: 1})
                total_validation_loss_error += batch_validation_loss_error
            ending_time = time.time()
            batch_time = ending_time - starting_time
            average_validation_loss_error = total_validation_loss_error / (len(validation_questions) / batch_size)
            print('Validation Loss Error: {:>6.3f}, Batch Validation Time: {:d} seconds'.format(average_validation_loss_error, int(batch_time)))
            learning_rate *= learning_rate_decay
            if learning_rate < min_learning_rate:
                learning_rate = min_learning_rate
            list_validation_loss_error.append(average_validation_loss_error)
            if average_validation_loss_error <= min(list_validation_loss_error):
                print('I speak better now!!')
                early_stopping_check = 0
                saver = tf.train.Saver()
                saver.save(session, checkpoint)
            else:
                print("Sorry I do not speak better, I need to practice more.")
                early_stopping_check += 1
                if early_stopping_check == early_stopping_stop:
                    break
    if early_stopping_check == early_stopping_stop:
        print("My apologies, I cannot speak better anymore. This is the best I can do.")
        break
print("Game Over")
 

In [110]:
########## PART 4 - TESTING THE SEQ2SEQ MODEL ##########
 
 
 
# Loading the weights and Running the session
checkpoint = "models/cornell_movie_dialog/trained_model_v1/best_weights_training.ckpt"
session = tf.InteractiveSession()
session.run(tf.global_variables_initializer())
saver = tf.train.Saver()
saver.restore(session, checkpoint)
 
# Converting the questions from strings to lists of encoding integers
def convert_string2int(question, word2int):
    question = clean_text(question)
    return [word2int.get(word, word2int['<OUT>']) for word in question.split()]
 
# Setting up the chat
while(True):
    question = input("You: ")
    if question == 'Goodbye':
        break
    question = convert_string2int(question, questionswords2int)
    question = question + [questionswords2int['<PAD>']] * (25 - len(question))
    fake_batch = np.zeros((batch_size, 25))
    fake_batch[0] = question
    predicted_answer = session.run(test_predictions, {inputs: fake_batch, keep_prob: 0.5})[0]
    answer = ''
    for i in np.argmax(predicted_answer, 1):
        if answersints2word[i] == 'i':
            token = ' I'
        elif answersints2word[i] == '<EOS>':
            token = '.'
        elif answersints2word[i] == '<OUT>':
            token = 'out'
        else:
            token = ' ' + answersints2word[i]
        answer += token
        if token == '.':
            break
    print('ChatBot: ' + answer)

NotFoundError: Key bidirectional_rnn/fw/multi_rnn_cell/cell_1/basic_lstm_cell/weights/Adam_1 not found in checkpoint
	 [[Node: save_3/RestoreV2_23 = RestoreV2[dtypes=[DT_FLOAT], _device="/job:localhost/replica:0/task:0/cpu:0"](_recv_save_3/Const_0, save_3/RestoreV2_23/tensor_names, save_3/RestoreV2_23/shape_and_slices)]]

Caused by op 'save_3/RestoreV2_23', defined at:
  File "C:\Users\Ident\anaconda3\envs\tf1.0\lib\runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "C:\Users\Ident\anaconda3\envs\tf1.0\lib\runpy.py", line 85, in _run_code
    exec(code, run_globals)
  File "C:\Users\Ident\anaconda3\envs\tf1.0\lib\site-packages\ipykernel_launcher.py", line 16, in <module>
    app.launch_new_instance()
  File "C:\Users\Ident\anaconda3\envs\tf1.0\lib\site-packages\traitlets\config\application.py", line 658, in launch_instance
    app.start()
  File "C:\Users\Ident\anaconda3\envs\tf1.0\lib\site-packages\ipykernel\kernelapp.py", line 499, in start
    self.io_loop.

In [ ]:
input()

In [ ]:
cd "C:\Users\Ident\Desktop\seq2seq-chatbot"

In [ ]:
python chat.py models/cornell_movie_dialog/trained_model_v1/best_weights_training.ckpt